In [1]:
import numpy as np
import pickle

# Function to load the dataset
def read_pkl(path):
    with open(path, 'rb') as f:
        data = pickle.load(f)
    return data

# Load the dataset
path = '/nas/Dataset/Phoenix/phoenix-2014-keypoints.pkl'  # Replace with your path
data = read_pkl(path)

# Check the dataset keys
print("Loaded dataset keys:", list(data.keys()))


Loaded dataset keys: ['fullFrame-210x260px/train/01April_2010_Thursday_heute_default-0/1/01April_2010_Thursday_heute', 'fullFrame-210x260px/train/01April_2010_Thursday_heute_default-2/1/01April_2010_Thursday_heute', 'fullFrame-210x260px/train/01April_2010_Thursday_heute_default-3/1/01April_2010_Thursday_heute', 'fullFrame-210x260px/train/01April_2010_Thursday_heute_default-4/1/01April_2010_Thursday_heute', 'fullFrame-210x260px/train/01April_2010_Thursday_heute_default-6/1/01April_2010_Thursday_heute', 'fullFrame-210x260px/train/01April_2010_Thursday_heute_default-7/1/01April_2010_Thursday_heute', 'fullFrame-210x260px/train/01April_2010_Thursday_heute_default-8/1/01April_2010_Thursday_heute', 'fullFrame-210x260px/train/01April_2010_Thursday_tagesschau_default-0/1/01April_2010_Thursday_tagesschau', 'fullFrame-210x260px/train/01April_2010_Thursday_tagesschau_default-2/1/01April_2010_Thursday_tagesschau', 'fullFrame-210x260px/train/01April_2010_Thursday_tagesschau_default-3/1/01April_2010_

In [2]:
# Quantize function
def quantize(value, threshold=0.3):
    if value > threshold:
        return 1
    elif value < -threshold:
        return -1
    else:
        return 0


In [3]:
# Function to process all videos with selective quantization (retain confidence scores)
def process_videos(data, threshold=5):
    deltas_data = {}      # Dictionary for raw deltas
    quantized_data = {}   # Dictionary for quantized deltas

    for video_key, video_data in data.items():
        print(f"Processing video: {video_key}")

        # Extract keypoints
        keypoints = video_data['keypoints']  # Shape: (frames, points, 3)
        frames, points, features = keypoints.shape

        # Step 1: Preallocate array for deltas
        deltas = np.zeros((frames - 1, points, features), dtype=np.float32)

        # Step 2: Calculate deltas (X, Y differences and mean confidence score)
        for i in range(1, frames):
            deltas[i - 1, :, 0] = keypoints[i, :, 0] - keypoints[i - 1, :, 0]  # X2 - X1
            deltas[i - 1, :, 1] = keypoints[i, :, 1] - keypoints[i - 1, :, 1]  # Y2 - Y1
            deltas[i - 1, :, 2] = (keypoints[i, :, 2] + keypoints[i - 1, :, 2]) / 2  # Mean of Conf

        # Step 3: Add a zero frame at the start ONCE for each video
        zero_frame = np.zeros((1, points, features), dtype=np.float32)  # Shape: (1, points, 3)
        deltas_with_zero = np.vstack((zero_frame, deltas))  # Add the zero frame at the start

        # Step 4: Quantize only X and Y deltas, retain confidence scores
        quantized_deltas = np.zeros_like(deltas_with_zero, dtype=np.float32)
        quantized_deltas[:, :, 0] = np.vectorize(quantize)(deltas_with_zero[:, :, 0], threshold)  # Quantize X
        quantized_deltas[:, :, 1] = np.vectorize(quantize)(deltas_with_zero[:, :, 1], threshold)  # Quantize Y
        quantized_deltas[:, :, 2] = deltas_with_zero[:, :, 2]  # Keep confidence scores as is

        # Step 5: Store the processed data in the original format
        deltas_data[video_key] = {'keypoints': deltas_with_zero}         # Raw deltas
        quantized_data[video_key] = {'keypoints': quantized_deltas}      # Quantized deltas with original confidence

    return deltas_data, quantized_data


In [4]:
# Process all videos
threshold = 0.3  # Threshold for quantization
deltas_data, quantized_data = process_videos(data, threshold=threshold)

# Check the processed output
print("Number of videos processed:", len(deltas_data))


Processing video: fullFrame-210x260px/train/01April_2010_Thursday_heute_default-0/1/01April_2010_Thursday_heute
Processing video: fullFrame-210x260px/train/01April_2010_Thursday_heute_default-2/1/01April_2010_Thursday_heute
Processing video: fullFrame-210x260px/train/01April_2010_Thursday_heute_default-3/1/01April_2010_Thursday_heute
Processing video: fullFrame-210x260px/train/01April_2010_Thursday_heute_default-4/1/01April_2010_Thursday_heute
Processing video: fullFrame-210x260px/train/01April_2010_Thursday_heute_default-6/1/01April_2010_Thursday_heute
Processing video: fullFrame-210x260px/train/01April_2010_Thursday_heute_default-7/1/01April_2010_Thursday_heute
Processing video: fullFrame-210x260px/train/01April_2010_Thursday_heute_default-8/1/01April_2010_Thursday_heute
Processing video: fullFrame-210x260px/train/01April_2010_Thursday_tagesschau_default-0/1/01April_2010_Thursday_tagesschau
Processing video: fullFrame-210x260px/train/01April_2010_Thursday_tagesschau_default-2/1/01Apr

In [5]:
# Function to save data to a pickle file
def save_pkl(data, output_path):
    with open(output_path, 'wb') as f:
        pickle.dump(data, f)
    print(f"Data saved to {output_path}")

# Save the processed data
save_pkl(deltas_data, '/nas/Chingiz/sing_language/delta/phoenix_deltas_all.pkl')            # File for raw deltas
save_pkl(quantized_data, '/nas/Chingiz/sing_language/vector/phoenix_quantized_all_conf_same.pkl')      # File for quantized deltas

Data saved to /nas/Chingiz/sing_language/delta/phoenix_deltas_all.pkl
Data saved to /nas/Chingiz/sing_language/vector/phoenix_quantized_all_conf_same.pkl


In [15]:
import pickle 
def read_pkl(path):
    with open(path, 'rb') as f:
        xxx = pickle.load(f)
    return xxx

path = '/nas/Chingiz/sing_language/delta/phoenix_deltas_all.pkl'
data_vector = read_pkl(path)
data_vector

{'fullFrame-210x260px/train/01April_2010_Thursday_heute_default-0/1/01April_2010_Thursday_heute': {'keypoints': array([[[  0.        ,   0.        ,   0.        ],
          [  0.        ,   0.        ,   0.        ],
          [  0.        ,   0.        ,   0.        ],
          ...,
          [  0.        ,   0.        ,   0.        ],
          [  0.        ,   0.        ,   0.        ],
          [  0.        ,   0.        ,   0.        ]],
  
         [[ -0.75      ,  -1.375     ,   0.9692383 ],
          [ -0.125     ,  -1.03125   ,   0.96972656],
          [ -0.375     ,  -1.1875    ,   0.9794922 ],
          ...,
          [  1.5625    ,  -3.75      ,   0.83496094],
          [  0.1875    ,  -4.25      ,   0.8720703 ],
          [ -0.875     ,  -4.375     ,   0.86621094]],
  
         [[ -0.625     ,  -0.875     ,   0.9609375 ],
          [ -0.3125    ,  -0.5       ,   0.96972656],
          [ -0.625     ,  -1.15625   ,   0.9707031 ],
          ...,
          [ -4.        , -1

In [7]:
data_vector.keys()

dict_keys(['fullFrame-210x260px/train/01April_2010_Thursday_heute_default-0/1/01April_2010_Thursday_heute', 'fullFrame-210x260px/train/01April_2010_Thursday_heute_default-2/1/01April_2010_Thursday_heute', 'fullFrame-210x260px/train/01April_2010_Thursday_heute_default-3/1/01April_2010_Thursday_heute', 'fullFrame-210x260px/train/01April_2010_Thursday_heute_default-4/1/01April_2010_Thursday_heute', 'fullFrame-210x260px/train/01April_2010_Thursday_heute_default-6/1/01April_2010_Thursday_heute', 'fullFrame-210x260px/train/01April_2010_Thursday_heute_default-7/1/01April_2010_Thursday_heute', 'fullFrame-210x260px/train/01April_2010_Thursday_heute_default-8/1/01April_2010_Thursday_heute', 'fullFrame-210x260px/train/01April_2010_Thursday_tagesschau_default-0/1/01April_2010_Thursday_tagesschau', 'fullFrame-210x260px/train/01April_2010_Thursday_tagesschau_default-2/1/01April_2010_Thursday_tagesschau', 'fullFrame-210x260px/train/01April_2010_Thursday_tagesschau_default-3/1/01April_2010_Thursday_ta

In [8]:
len(data_vector.keys())  

6841

In [9]:
data_vector['fullFrame-210x260px/train/29March_2011_Tuesday_tagesschau_default-22/1/29March_2011_Tuesday_tagesschau']

{'keypoints': array([[[ 0.        ,  0.        ,  0.        ],
         [ 0.        ,  0.        ,  0.        ],
         [ 0.        ,  0.        ,  0.        ],
         ...,
         [ 0.        ,  0.        ,  0.        ],
         [ 0.        ,  0.        ,  0.        ],
         [ 0.        ,  0.        ,  0.        ]],
 
        [[-1.        ,  0.        ,  0.9550781 ],
         [-1.        ,  0.        ,  0.97558594],
         [-1.        ,  0.        ,  0.9638672 ],
         ...,
         [-1.        ,  1.        ,  0.07946777],
         [ 1.        ,  1.        ,  0.06799316],
         [ 1.        ,  1.        ,  0.07427979]],
 
        [[-1.        ,  0.        ,  0.9394531 ],
         [-1.        ,  0.        ,  0.9794922 ],
         [-1.        ,  0.        ,  0.9838867 ],
         ...,
         [ 1.        , -1.        ,  0.1595459 ],
         [ 1.        , -1.        ,  0.14453125],
         [ 1.        , -1.        ,  0.14782715]],
 
        ...,
 
        [[-1.        

In [10]:
data_vector['fullFrame-210x260px/train/29March_2011_Tuesday_tagesschau_default-22/1/29March_2011_Tuesday_tagesschau']["keypoints"][1][100]


array([1.        , 1.        , 0.09918213], dtype=float32)

In [11]:
data_vector['fullFrame-210x260px/train/29March_2011_Tuesday_tagesschau_default-22/1/29March_2011_Tuesday_tagesschau']["keypoints"][0][100]

array([0., 0., 0.], dtype=float32)

In [12]:
data_vector['fullFrame-210x260px/train/29March_2011_Tuesday_tagesschau_default-22/1/29March_2011_Tuesday_tagesschau']["keypoints"][2][100]


array([-1.        , -1.        ,  0.11029053], dtype=float32)

In [13]:
data_vector['fullFrame-210x260px/train/29March_2011_Tuesday_tagesschau_default-22/1/29March_2011_Tuesday_tagesschau']["keypoints"][3][100]

array([-1.        , -1.        ,  0.10089111], dtype=float32)